We build a neural network (NN) for predicting diabete status from personal and clinical information. We use the most fundamental architecture called a multilayer perceptron (MLP) or more generally a densely connected NN.

In [ ]:
# Pima Indians onset of diabetes dataset
# Medical record data for Pima Indians and whether they had an onset of diabetes within five years.
# https://raw.githubusercontent.com/jbrownlee/Datasets/master/pima-indians-diabetes.data.csv
# https://machinelearningmastery.com/develop-your-first-neural-network-with-pytorch-step-by-step/
# https://pytorch.org/tutorials/beginner/introyt/trainingyt.html

# NumPy library to load your dataset
# PyTorch library for deep learning models.
import numpy as np
import torch
import torch.nn as nn
import torch.optim as optim

# PyTorch TensorBoard support
# from torch.utils.tensorboard import SummaryWriter
# import torchvision
# import torchvision.transforms as transforms

from datetime import datetime

import torchvision
import torchvision.transforms as transforms

In [ ]:
# load the dataset, split into input (X) and output (y) variables
### Input variables to be stored into X
# Number of times pregnant
# Plasma glucose concentration at 2 hours in an oral glucose tolerance test
# Diastolic blood pressure (mm Hg)
# Triceps skin fold thickness (mm)
# 2-hour serum insulin (μIU/ml)
# Body mass index (weight in kg/(height in m)2)
# Diabetes pedigree function
# Age (years)
### Output variable to be stored into y
# Class label (0 or 1)

dataset = np.loadtxt('https://raw.githubusercontent.com/jbrownlee/Datasets/master/pima-indians-diabetes.data.csv', delimiter=',')
X = dataset[:,0:8]
y = dataset[:,8]

X = torch.tensor(X, dtype=torch.float32)
y = torch.tensor(y, dtype=torch.float32).reshape(-1, 1)

In [ ]:
# Define the Linear Model (creating a Python class inherited from the nn.Module)
# it's more verbose but has some advantages
class PimaLinearClassifier(nn.Module):
    def __init__(self):
        super().__init__()
        self.hidden1 = nn.Linear(8, 12)
        self.hidden2 = nn.Linear(12, 8)
        self.output = nn.Linear(8, 1)
        self.act_output = nn.Sigmoid()

    def forward(self, x):
        x = self.hidden1(x)
        x = self.hidden2(x)
        x = self.act_output(self.output(x))
        # x = self.act_output(self.output(self.act2(self.hidden2(self.act1(self.hidden1(x))))))
        return x

model = PimaLinearClassifier()
print(model)

PimaLinearClassifier(
  (hidden1): Linear(in_features=8, out_features=12, bias=True)
  (hidden2): Linear(in_features=12, out_features=8, bias=True)
  (output): Linear(in_features=8, out_features=1, bias=True)
  (act_output): Sigmoid()
)


In [ ]:
# Define the Model (creating a Python class inherited from the nn.Module)
# it's more verbose but has some advantages
class PimaClassifier(nn.Module):
    def __init__(self):
        super().__init__()
        self.hidden1 = nn.Linear(8, 12)
        self.act1 = nn.ReLU()
        self.hidden2 = nn.Linear(12, 8)
        self.act2 = nn.ReLU()
        self.output = nn.Linear(8, 1)
        self.act_output = nn.Sigmoid()

    def forward(self, x):
        x = self.act1(self.hidden1(x))
        x = self.act2(self.hidden2(x))
        x = self.act_output(self.output(x))
        # x = self.act_output(self.output(self.act2(self.hidden2(self.act1(self.hidden1(x))))))
        return x

model = PimaClassifier()
print(model)

PimaClassifier(
  (hidden1): Linear(in_features=8, out_features=12, bias=True)
  (act1): ReLU()
  (hidden2): Linear(in_features=12, out_features=8, bias=True)
  (act2): ReLU()
  (output): Linear(in_features=8, out_features=1, bias=True)
  (act_output): Sigmoid()
)


In [ ]:
# Goal of the training!
# The loss function is the metric to measure the prediction’s distance to.
# In this example, a binary cross entropy (BCE) is used
# The optimizer is the algorithm you use to adjust the model weights progressively to produce a better output.
loss_fn = nn.BCELoss()
optimizer = optim.Adam(model.parameters(), lr=0.001)

In [ ]:
# We want to upgrade our training scheme, to look at the training and test datasets.
# Use of classes and functions may seem complicated initially, esp pay attention to errors related to dimensions and data types.
# But in the end, it'll help us think about the training in a higher level abstraction.

class DiabeteDataset():
    def __init__(self, X, y, transform=None):
        self.X = torch.tensor(X, dtype=torch.float32)
        self.y = torch.tensor(y, dtype=torch.float32).reshape(-1, 1)
        self.transform = transform

    def __len__(self):
        return len(self.y)

    def __getitem__(self, idx):
        if torch.is_tensor(idx):
            idx = idx.tolist()

        X = self.X
        y = self.y
        sample = {'X': X, 'y': y}

        if self.transform:
            sample = self.transform(sample)

        return sample

DatasetC = DiabeteDataset(X,y)

<ipython-input-6-ac450e17bc0f>:7: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  self.X = torch.tensor(X, dtype=torch.float32)
<ipython-input-6-ac450e17bc0f>:8: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  self.y = torch.tensor(y, dtype=torch.float32).reshape(-1, 1)


In [ ]:
# the full data is split into train and test, by using pytorch random_split
train_size = int(0.8 * len(DatasetC))
test_size = len(DatasetC) - train_size
train_dataset, test_dataset = torch.utils.data.random_split(DatasetC, [train_size, test_size])

# Create data loaders for our datasets; shuffle for training, not for validation
train_loader = torch.utils.data.DataLoader(train_dataset, batch_size=10, shuffle=True)
test_loader = torch.utils.data.DataLoader(test_dataset, batch_size=10, shuffle=False)

# Report split sizes
print('Training set has {} instances'.format(len(train_dataset)))
print('Validation set has {} instances'.format(len(test_dataset)))

Training set has 614 instances
Validation set has 154 instances


In [ ]:
# defining a function for training ONE epoch, going through batches
def train_one_epoch(epoch_index):
    running_loss = 0.
    last_loss = 0.

    # Here, we use enumerate(training_loader) to track the batch index and report some stats inbetween epochs
    for i, data in enumerate(train_dataset):
        #print(i)
        # Every data instance is an input + label pair
        Xtmp = data['X']
        ytmp = data['y']

        # Zero your gradients for every batch!
        optimizer.zero_grad()

        # Make predictions for this batch
        outputs = model(Xtmp)

        # Compute the loss and its gradients
        loss = loss_fn(outputs, ytmp)
        loss.backward()

        # Adjust learning weights
        optimizer.step()

        # Gather data and report
        running_loss += loss.item()
        avg_loss = running_loss / (i+1)

    return avg_loss

In [ ]:
# now we want to run MANY epochs. So we need to create a for-loop
# importantly,
timestamp = datetime.now().strftime('%Y%m%d_%H%M%S')
#writer = SummaryWriter('runs/fashion_trainer_{}'.format(timestamp))
epoch_number = 0

EPOCHS = 10

best_vloss = 1_000_000.

for epoch in range(EPOCHS):
    print('EPOCH {}:'.format(epoch_number + 1))

    # Make sure gradient tracking is on, and do a pass over the data
    model.train(True)
    avg_loss = train_one_epoch(epoch_number)

    # We don't need gradients on to do reporting
    model.train(False)

    running_vloss = 0.0
    for i, vdata in enumerate(test_loader):
        vinputs = vdata['X']
        vlabels = vdata['y']
        #vinputs, vlabels = vdata
        voutputs = model(vinputs)
        vloss = loss_fn(voutputs, vlabels)
        running_vloss += vloss

    avg_vloss = running_vloss / (i + 1)
    print('LOSS train {} valid {}'.format(avg_loss, avg_vloss))

    # Track best performance, and save the model's state
    if avg_vloss < best_vloss:
        best_vloss = avg_vloss
        model_path = 'model_{}_{}'.format(timestamp, epoch_number)
        torch.save(model.state_dict(), model_path)

    epoch_number += 1

EPOCH 1:
LOSS train 0.6422580332049329 valid 0.5415539145469666
EPOCH 2:
LOSS train 0.5079472670240589 valid 0.48134127259254456
EPOCH 3:
LOSS train 0.4522133653055185 valid 0.42791983485221863
EPOCH 4:
LOSS train 0.4138989887816122 valid 0.4020896255970001
EPOCH 5:
LOSS train 0.393661891258889 valid 0.38541853427886963
EPOCH 6:
LOSS train 0.3789223202470848 valid 0.3722020983695984
EPOCH 7:
LOSS train 0.36615370024687305 valid 0.36209017038345337
EPOCH 8:
LOSS train 0.359885427579041 valid 0.35813650488853455
EPOCH 9:
LOSS train 0.35528331218402626 valid 0.3531974256038666
EPOCH 10:
LOSS train 0.3523066516613727 valid 0.35149529576301575


In [ ]:
# compute the overall, final compute accuracy (no_grad is optional)
with torch.no_grad():
    y_pred = model(X)

accuracy = (y_pred.round() == y).float().mean()
print(f"Accuracy {accuracy}")

Accuracy 0.8411458134651184
